In [1]:
import sys
sys.path.append('../')

In [12]:
from Proximity import prox_model, Proximity_Indicator
from brix import Indicator, Handler, Grid_maker
import US_State
import datetime
import geopandas as gpd
import json
import requests

# In this example, we will:
    - download some census data filtered to the area surrounding the grid
    - create and deploy a proximity indicator

In [3]:
table_name='epa'
state_fips=6
geom_type='block'

# Set up a back end module

### Create the Handler

In [4]:
H=Handler(table_name)

https://cityio.media.mit.edu/api/tables/list/ Attempt: 0
https://cityio.media.mit.edu/api/table/epa/meta/hashes/ Attempt: 0


To intialise the proximity indicator, we need geodataframes of (i) the static places/POIs and (ii) the GEOGRID

In [5]:
geogrid=H.get_geogrid_data(include_geometries=True).as_df()

https://cityio.media.mit.edu/api/table/epa/GEOGRIDDATA/ Attempt: 0
https://cityio.media.mit.edu/api/table/epa/GEOGRID/ Attempt: 0


/opt/anaconda3/envs/prox/lib/python3.10/site-packages/brix/classes.py:981: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  geos = gpd.GeoDataFrame(geos.drop('geometry',1),geometry=geos['geometry'].apply(lambda x: shape(x))) # no crs to avoid warning
/opt/anaconda3/envs/prox/lib/python3.10/site-packages/brix/classes.py:251: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  geogrid_data = gpd.GeoDataFrame(geogrid_data.drop('geometry',1),geometry=geogrid_data['geometry'].apply(lambda x: shape(x)),crs='EPSG:4326')


### Get some baseline places data by downloading geometres and demographic data from census

In [9]:
lon, lat = geogrid.unary_union.centroid.x, geogrid.unary_union.centroid.y

In [13]:
st=US_State.US_State(state_fips=state_fips, year=2019, geom_type=geom_type)
st.get_geometry()
st.get_lodes_data( include=['wac', 'rac'])
st.add_lodes_cols_to_shape()

Getting geometry (block) for state: California


/Users/ronandoorley/Documents/Media_Lab/CityScope/CS_Spatial_Modules/examples/../US_State.py:54: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroids=self.geom['geometry'].centroid


Getting WAC data from https://lehd.ces.census.gov/data/lodes/LODES7/
	 Formatting WAC data
Getting RAC data from https://lehd.ces.census.gov/data/lodes/LODES7/
	 Formatting RAC data


Subset the geometry by distance from the grid to reduce the size 

In [14]:
st.subset_geom_by_distance(centre_x_y=[lon, lat], 
                                   radius=5000, name='model_area')
zones_subset=st.return_geometry('model_area')
zones_subset.explore()

	 Subsetting zones by distance


### Define the proximity targets
- column is the column of the GeoDataFrame corresponding to this POI. The column can be binary (indicating whther the row is one these POIs) or numerical (indicating the capacity of the POI contained in this place.
- 'from' represents the relevant source location for this POI. eg. if we want a POI (eg. employment) to be located close to where people live, then 'from' should be the column representing residential population.
- 'max' is used in the linear normalisation of indicators. If the proximity result is equal to or greater than the max, the score will be 1.

In [15]:
target_settings={'housing': {'column': 'res_total','max': 100000, 'from': 'emp_total'},
                 'healthcare': {'column': 'emp_naics_62','max': 10000, 'from': 'res_total'},
                 'jobs': {'column': 'emp_total','max': 100000, 'from': 'res_total'},
                'shopping': {'column': 'emp_naics_44-45','max': 10000, 'from': 'res_total'},
                'education': {'column': 'emp_naics_61','max': 10000, 'from': 'res_total'},
                'entertainment': {'column': 'emp_naics_71','max': 10000, 'from': 'res_total'}}

### Create the proximity indicator.
- 'max_dist' is the network search radius in meters. eg. for 15 minutes walking accessibility, use max_dist=1200 (assuming average espeed of 4.8km/hr)

In [ ]:
p=Proximity_Indicator(static_places=zones_subset, geogrid=geogrid, 
                      max_dist=2400, target_settings=target_settings)

In [ ]:
H.add_indicator(p)
H.listen()